# Chipping images with gbdxtools

This notebook walks the user through some different methods for dividing satellite images into more easily digestable chips using gbdxtools, a Python package that simplifies working with DigitalGlobe's GBDX platform. Check out [this link](https://gbdxtools.readthedocs.io/en/latest/api_reference.html#catalogimage) to read more about gbdxtools.

To demonstrate the different chipping methods of gbdxtools, we will be working with burned building data from the November 2018 Woosley Fire in California.  In addition to working with satellite imagery, we will also be importing polygons of burned buildings and showing how these can be used to make chips.

But before looking at the data, let's import all of our necessary Python modules.

In [ ]:
# Import modules

# GBDXTools modules
from gbdxtools import Interface, CatalogImage, LineStyle, MatchExpression
gbdx=Interface()

# Basic modules
import os
from os.path import isfile, join
import io
import numpy as np
import matplotlib.pyplot as plt
import json
import requests
import random

# Modules for interacting with chips
from shapely.geometry import box, shape, mapping
import dask.array as da
from PIL import Image

# Modules for accessing data on s3
import boto3
from botocore.exceptions import ClientError
import json

# Module for creating progress bars to track chip creation
try:
    from tqdm import tqdm_notebook as tqdm
except:
    !pip install tqdm
    from tqdm import tqdm_notebook as tqdm
    
print('Imported all modules.')

### Importing the imagery

To import our imagery, we can use a wrapper class from gbdxtools called CatalogImage. This class outputs an image as a [Dask array](https://docs.dask.org/en/latest/array.html), which can be interacted with very similarly to a NumPy array, but is more ideal for larger datasets such as multispectral images. 

The only required parameter for a **CatalogImage** instance is a catalog ID which is unique to each catalog image. Additionally, we can also tell **CatalogImage** to perform some initial processing for us, including pansharpening, atmospheric compensation, and dynamic range adjustment. If these are not specified, **CatalogImage** will return the raw image. These terms are briefly defined as follows:

__Pansharpening__: Process of merging the higher spatial resolution panchromatic image with the higher spectral resolution multispectral image. Results in a crisper image but changes the pixel values in the multispectral image. Reduces atmospheric distortion but changes the original pixel values.

__Atmospheric compensation (acomp)__: Process of removing image artifacts created by particles and vapor in the atmosphere.

__Dynamic range adjustment (DRA)__: Process of converting pixel values of an orthorectified, acomped, pansharpened image from 16 bits to 8 bits. Allows the image to be viewed on a computer screen.

Whether or not these processing steps can be performed on an image depends on the satellite that collected the image and how it was collected. For example, WorldView-1 performs panchromatic imaging but not multispectral, and therefore pansharpening is not applicable. The cell below checks that these steps can be performed and then returns a pansharped image that has had acomp and DRA applied. 

Since our catalog image is quite large, we will crop it to the area where we have burned building information, in northern Malibu.

In [ ]:
# Define area of interest
north_malibu_bbox = [-118.81, 34.03, 
                     -118.76, 34.06]

# Download multispectral image of burned area
cat_id = '103001008513F200'
if not CatalogImage.is_ordered(cat_id):
    print('Catalog image must be ordered before continuing.')

# Check that acomp can be performed on image
acomp = CatalogImage.acomp_available(cat_id)

# Check that pansharping and DRA can be performed on image
# Import image from catalog
pansharpen = True 
dra = True
try:
    img = CatalogImage(cat_id, bbox = north_malibu_bbox, 
                       pansharpen = pansharpen, acomp = acomp, dra = dra)
except:
    img = CatalogImage(cat_id, bbox = north_malibu_bbox, acomp=acomp)
    
print('Collected image from catalog.')

We can check out the image using the **preview** function. This produces a slippy map that we can zoom in and out.

In [ ]:
# Check out image
img.preview()

### Importing polygons from a geoJSON

One way in which we might want to create chips is by centering them around features of interest. For example, we might want to have chips from the Woosley fire which contain affected buildings. Here we will demonstrate how to import a geoJSON containing information about buildings that were burned by the Woosley fire. GeoJSONs provide a simple way for encoding a variety of geographic data structures, such as burned building polygons, and they follow [this convention](https://geojson.org/). The two easiest ways to import a geoJSON into our Jupyter Notebook are by importing from a local directory or from an Amazon S3 bucket. The next two cells demonstrate each of these methods.

In [ ]:
# Import data locally
with open('woosley_classification.geojson') as json_file:
    features_dict = json.load(json_file)

print('%i features in geoJSON.' % len(features_dict['features']))

In [ ]:
# Alternatively, import data from s3 bucket
s3_location = 'https://s3.amazonaws.com/veda-storage-sagemaker/woosley_classification.geojson'
response = requests.get(s3_location)
features_dict = json.loads(response.content)

print('%i features in geoJSON.' % len(features_dict['features']))

Both methods result in the geoJSON being imported as a dictionary that contains 177 features. Each feature corresponds to a building. We can look at the first feature by running the cell below. Here, we see that each feature tells us whether or not the building is still standing or burned to the ground (signified by a 'burned' value of 0 or 1, respectively, or a label of 'not_burned_building' or 'burned_building', respectively). The feature also gives the geometry of the building as a polygon of many points, where each point has latitude and longitude coordinates. 

In [ ]:
features_dict['features'][0]

We can easily visualize the building polygon by using the geometric information of the feature to create a Shapely shape object.

In [ ]:
shape(features_dict['features'][0]['geometry'])

To create chips that contain only buildings which were burned to the ground by the fire, we first need to separate the features dictionary into burned features and not burned features. This is done in the next cell.

In [ ]:
# Split features into burned and not burned buildings
burned = 1 # burned building label in features_dict
not_burned = 0 # not burned building label in features_dict

burned_features = []
not_burned_features = []
labels = []
for feature in features_dict['features']:
    if feature['properties']['label'] not in labels:
        labels.append(feature['properties']['label'])
        
    if feature['properties']['burned'] == burned:
        burned_features.append(feature)
    elif feature['properties']['burned'] == not_burned:
        not_burned_features.append(feature)
    else:
        feature_ID = feature['properties']['index1']
        print('Unrecognized class for feature %i.' % feature_ID)

burned_features_dict = {'features': burned_features}
not_burned_features_dict = {'features': not_burned_features}

print('Features consist of %i burned and %i not burned buildings.'
      % (len(burned_features), len(not_burned_features)))
print('Feature label(s): %s' % labels)

Now we see that all 177 features from the geoJSON belong to burned buildings. These features are now stored in a list called __burned_features__. The next step is seeing where these buildings are on the image we imported from the catalog. Rather than using the __preview__ function again, which just allows us to look at the catalog image, we can use the __map__ function from gbdxtool's __Vector__ class. Just like with the __preview__ function, this allows us to zoom in and out on the resulting map, while also highlighting the burned buildings in a style of our choice. 

The __map__ function gives us the option of using the image we downloaded, so that we can compare the burned areas to our burned building polygons. However, this causes the slippy map to take longer to load (the next cell takes about a minute to load), so we won't do this for future slippy maps. If no image is specified, the slippy map will use a default image of the area that loads a lot faster.

In [ ]:
# Map burned buildings
gbdx.vectors.map(features=burned_features, 
                 styles=LineStyle(color="red", width=5), 
                 zoom=13, image=img)

### Creating chips with the __window_at__ function

We are going to go through three different methods of making chips with gbdxtools. The first is __window_at__, a function which returns a chip of a specified pixel size that is centered on a geometry object, like a building polygon. This function is especially useful for creating training data that contains specific features for a machine learning model. 

Running the cell below creates 177 chips, each 256 pixels high by 256 pixels wide and centered on a burned building from the geoJSON. The __chip_size__ variable can be adjusted to create smaller or larger chips, but the width and height should both be divisible by 8. The generated chips are originally Dask objects, which have the image bands and their pixels organized into a Dask array and also keep the image metadata intact. This is great, but if we want to plot these images using matplotlib for example, we need to separate out the RGB bands from the Dask object and store them into a numpy array. This is done by appending __.rgb()__ on to the chip and reformatting it as a numpy array.

In [ ]:
# Get burned building outlines as shape objects from features_dict
obj_outlines = []
for feature in burned_features:
    outline = shape(feature['geometry'])
    obj_outlines.append(outline) 

# Create chips using window_at() -- chips containing buildings
chip_size = (256,256)
image_chips = []
dask_chips = []
pbar = tqdm(total=len(burned_features), desc='Progress')
for i,feature in enumerate(burned_features):
    try:
        chip = img.window_at(obj_outlines[i], chip_size)
        image_chips.append(np.array(chip.rgb())) # reformat data so it can be plotted
        dask_chips.append(chip) # store the dask array because it has image metadata in it
        pbar.update(1)
    except(ValueError): 
        pass
    except(StopIteration):
        break
pbar.close()

If we map the original chips as shape objects, we see that they are indeed centered on the burned buildings from our geoJSON. 

In [ ]:
# Store chip geometries as list of dictionaries with same syntax as geoJSON
chips_dict = []
chip_id = len(burned_features)
for chip in dask_chips:
    coords = chip.bounds
    coords_box = mapping(box(*coords))
    coords_box['coordinates'] = [coords_box['coordinates'][0]]
    chips_dict.append({'type': 'Feature',
                       'properties': {'index1': chip_id, 'label': 'chip'},
                       'geometry': coords_box})
    chip_id += 1

# Create list containing both list of chip dictionaries and list of
# burned building dictionaries
combined_list = burned_features.copy()
for feature in chips_dict:
    combined_list.append(feature)
    
# Define MatchExpressions of different LineStyle parameters for slippy map
line_colors = MatchExpression(property_name='label',
                              values={'burned_building': 'red',
                                      'chip': 'blue'},
                              default_value='#ff0000')
line_widths = MatchExpression(property_name='label',
                              values={'burned_building': 5,
                                      'chip': 3},
                              default_value=3)

# Map chips and burned buildings
gbdx.vectors.map(features=combined_list, 
                 styles=LineStyle(color=line_colors, width=line_widths),
                 zoom=13)

In addition to using a slippy map, we can visualize what each chip looks like by plotting the reformatted chips with matplotlib.

In [ ]:
# Plot random chips
i = int(random.uniform(0,len(image_chips)))
plt.figure(figsize=(6,6))
plt.imshow(image_chips[i])
plt.title('Index = %i' % i)
plt.axis('off')
plt.show()

### Creating chips with the __window_cover__ function

The next gbdxtools chipping method we are going to go through is __window_cover__, which divides the image into a grid of tiles of some specified size. While __window_at__ returned one chip, __window_cover__ returns something called a chip generator which can be iteratively called to return mutliple chips. This function is useful for creating background data for a machine learning model which does not contain the feature the model is supposed to detect.

Running the cell below creates 20 chips, each 256 pixels high by 256 pixels wide. The __desired_chip_count__ variable can be adjusted to generate more or less chips. As with __window_at__, these chips are Dask objects, which we will also save as numpy arrays. 

In [ ]:
# Create chips using img.window_cover() -- chips from catalog image without buildings
desired_chip_count = 20
chip_size=(256,256)

chip_generator = img.window_cover(chip_size, pad=False)
image_chips = []
dask_chips = []
chip_count = 0

pbar = tqdm(total=desired_chip_count, desc='Progress')   
while chip_count < desired_chip_count:
    try:
        chip = next(chip_generator)
        image_chips.append(chip.rgb())
        dask_chips.append(chip)
        chip_count += 1
        pbar.update(1)
    except StopIteration:
        break
pbar.close()

If we were trying to create background data for a burned building detection model, we would want to complete an extra step after creating our chips which removes any chips containing burned buildings. We can do this by taking our list of building polygons stored in __obj_outlines__ and checking if any of our newly created chips intersect with these polygons using the Shapely __intersect__ function. Then we can create a new list of background chips which do not contain those chips that intersected. 

If we run the cell below, we see that none of the 20 chips we generated intersect with our building polygons, so all 20 were returned in the new variable __bkgd_dask_chips__.

In [ ]:
# Look for chips that contain known burned buildings and remove from list  
skip_chip_indx = [] 
pbar = tqdm(total=len(dask_chips), desc='Progress')
for i in range(len(dask_chips)):
    geoms = []
    tile_outline = box(*dask_chips[i].bounds)
    for j,obj_outline in enumerate(obj_outlines):
        if tile_outline.intersects(obj_outline):
            if i not in skip_chip_indx:
                skip_chip_indx.append(i)
    pbar.update(1)
pbar.close()

print('Number of chips with known burned buildings in them: %i' 
      % len(skip_chip_indx))

# Sort out chips not in this list
bkgd_dask_chips = [] # list of dask chips
for i, chip in enumerate(dask_chips):
    if i not in skip_chip_indx:
        bkgd_dask_chips.append(dask_chips[i])
        
print('%i chips returned.' % len(bkgd_dask_chips))

By plotting all of the background chips on a slippy map, we can verify that they do not intersect any of the burned buildings from our geoJSON. We also see how these chips were generated by starting at one corner of the catalog image and moving from left to right. This is good if we want our chips generated in a more systematic way, but it also means that we would need to generate more than 20 chips if we wanted our background data to represent all of the variation in the background image. That's where the next chipping method becomes useful.

In [ ]:
# Store chip geometries as list of dictionaries with same syntax as geoJSON
chips_dict = []
chip_id = 0
for chip in bkgd_dask_chips:
    coords = chip.bounds
    coords_box = mapping(box(*coords))
    coords_box['coordinates'] = [coords_box['coordinates'][0]]
    chips_dict.append({'type': 'Feature',
                       'properties': {'index1': chip_id, 'label': 'chip'},
                       'geometry': coords_box})
    chip_id += 1

# Create list containing both list of chip dictionaries and list of
# burned building dictionaries
combined_list = burned_features.copy()
for feature in chips_dict:
    combined_list.append(feature)
    
# Define MatchExpressions of different LineStyle parameters for slippy map
line_colors = MatchExpression(property_name='label',
                              values={'burned_building': 'red',
                                      'chip': 'blue'},
                              default_value='#ff0000')
line_widths = MatchExpression(property_name='label',
                              values={'burned_building': 5,
                                      'chip': 3},
                              default_value=3)

# Map chips and burned buildings
gbdx.vectors.map(features=combined_list, 
                 styles=LineStyle(color=line_colors, width=line_widths),
                 zoom=13)

### Creating chips with the __iterwindows__ function

The third and final gbdxtools chipping method we are going to go through is __iterwindows__, which iterates over random windows in the image to generate tiles of some specified size. Like __window_cover__, __iterwindows__ returns a chip generator that must be iteratively called to return mutliple chips. This function is especially useful for creating background data, because the random selection of windows means that more of the image is likely to be represented in the dataset.

Running the cell below creates 20 chips, each 256 pixels high by 256 pixels wide.

In [ ]:
# Create chips by iterating over random windows
desired_chip_count = 20
chip_size=(256,256)
chip_count = 0
image_chips = []
dask_chips = []

pbar = tqdm(total=desired_chip_count, desc='Progress')
chip_generator = img.iterwindows(count = desired_chip_count,
                                 window_shape = chip_size)
while chip_count < desired_chip_count:
    chip = next(chip_generator)
    image_chips.append(chip.rgb())
    dask_chips.append(chip)
    chip_count += 1
    pbar.update(1)
pbar.close()

Like with the last method, we can remove any chips that intersect burned buildings and plot them a slippy map. Here, we see the random nature of these windows, as well as how none of them overlap with the burned buildings plotted in red.

In [ ]:
# Look for chips that contain known burned buildings and remove from list  
skip_chip_indx = [] 
pbar = tqdm(total=len(dask_chips), desc='Progress')
for i in range(len(dask_chips)):
    geoms = []
    tile_outline = box(*dask_chips[i].bounds)
    for j,obj_outline in enumerate(obj_outlines):
        if tile_outline.intersects(obj_outline):
            if i not in skip_chip_indx:
                skip_chip_indx.append(i)
    pbar.update(1)
pbar.close()

print('Number of chips with known burned buildings in them: %i' 
      % len(skip_chip_indx))

# Sort out chips not in this list
bkgd_dask_chips = [] # list of dask chips
for i in range(desired_chip_count):
    if i not in skip_chip_indx:
        bkgd_dask_chips.append(dask_chips[i])
        
print('%i chips returned.' % len(bkgd_dask_chips))

# Store chip geometries as list of dictionaries with same syntax as geoJSON
chips_dict = []
chip_id = len(burned_features)
for chip in bkgd_dask_chips:
    coords = chip.bounds
    coords_box = mapping(box(*coords))
    coords_box['coordinates'] = [coords_box['coordinates'][0]]
    chips_dict.append({'type': 'Feature',
                       'properties': {'index1': chip_id, 'label': 'chip'},
                       'geometry': coords_box})
    chip_id += 1

# Create list containing both list of chip dictionaries and list of
# burned building dictionaries
combined_list = burned_features.copy()
for feature in chips_dict:
    combined_list.append(feature)
    
# Define MatchExpressions of different LineStyle parameters for slippy map
line_colors = MatchExpression(property_name='label',
                              values={'burned_building': 'red',
                                      'chip': 'blue'},
                              default_value='#ff0000')
line_widths = MatchExpression(property_name='label',
                              values={'burned_building': 5,
                                      'chip': 3},
                              default_value=3)

# Map chips and burned buildings
gbdx.vectors.map(features=combined_list, 
                 styles=LineStyle(color=line_colors, width=line_widths),
                 zoom=13)

### Saving chips

The final step in creating chips with gbdxtools is saving them so that they can be used later. As with importing the geoJSON, saving can be done both locally and with an S3 bucket. The next two cells demonstrate both. It should be noted that these two methods only show how chips can be saved as PNG files-- if their geographic information needs to be left intact, they will need to be saved as geoTIFFs. 

In [ ]:
# Save chips locally

# Create data directory if it does not already exist
data_dir = './woosley_chips' # local directory to store chips in
if not os.path.exists(data_dir):
    os.makedirs(data_dir)

# Plot each backround chip and save to data_dir
image_chips = [chip.rgb() for chip in bkgd_dask_chips]
pbar = tqdm(total=len(image_chips), desc='Progress')
chip_n = 0
for i in range(len(image_chips)):
    fig = plt.figure()
    plt.imshow(image_chips[i])
    plt.axis('off')
    plt.tight_layout()
    fig.savefig('%s/chip_%i.png' % (data_dir, chip_n))
    plt.close(fig)
    chip_n += 1
    pbar.update(1)
pbar.close()

We can check that this worked by clicking on the "File" tab above, selecting "Open...", and verifying that there is a folder called "woosley_chips" that contains 20 chip PNGs.

The class __S3__ in gbdxtools has an __upload__ method which allows files to be easily uploaded. This method requires that the file first be created locally first, so the previous cell must be run before running the next cell.

In [ ]:
# Upload chip to S3
chip_n = 0 # index of chip to upload
chip_local_path = './woosley_chips/chip_%i.png' % chip_n # location of chip locally
s3_save_folder = 'chipping_demo' # folder to save to in S3 -- does need to already exist
chip_s3_path = gbdx.s3.upload(local_file = chip_local_path, 
                              s3_path = '%s/chip_%i.png' % (s3_save_folder, chip_n))

print('Location of chip in S3:', chip_s3_path)

To check that the chip was correctly uploaded, we can also download it using gbdxtools, and plot it with Pillow. 

In [ ]:
# Create download directory if it does not already exist
download_dir = './s3_downloads' # local directory to store chips in
if not os.path.exists(download_dir):
    os.makedirs(download_dir)

# Download image from S3 into download directory
chip_n = 0
gbdx.s3.download(location = 'chipping_demo/chip_%i.png' % chip_n,
                 local_dir = download_dir)

# Import image from download directory and plot
chip_download_path = '%s/chip_%i.png' % (download_dir, chip_n)
Image.open(chip_download_path)

The image has been successfully uploaded to S3. Now we have all the steps necessary for creating chips with gbdxtools!